## Municiaplity Download link:

https://gis-mdc.opendata.arcgis.com/datasets/MDC::municipal-boundary/explore?location=25.557077%2C-80.458171%2C9.44

In [1]:
import pandas as pd
import geopandas as gpd

In [2]:
deals_df = pd.read_csv('Adam F. - 2025 Miami Brokerage and Broker Rankings - Agents_Brokers.csv')
muni_gdf = gpd.read_file('Municipalitypoly_gdb_-3974701052066827405.geojson')

In [3]:
deals_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26946 entries, 0 to 26945
Data columns (total 22 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Unique_ID       26946 non-null  object 
 1   mlsId           26946 non-null  object 
 2   Property_ID     26844 non-null  float64
 3   Address         26946 non-null  object 
 4   price           26946 non-null  int64  
 5   Side            26946 non-null  object 
 6   Brokerage_Firm  26574 non-null  object 
 7   zipcode         26817 non-null  float64
 8   Agent_Name      26553 non-null  object 
 9   TRD_note        117 non-null    object 
 10  city            26844 non-null  object 
 11  latitude        26844 non-null  float64
 12  longitude       26844 non-null  float64
 13  Unnamed: 13     0 non-null      float64
 14  Unnamed: 14     0 non-null      float64
 15  Unnamed: 15     0 non-null      float64
 16  Unnamed: 16     0 non-null      float64
 17  Unnamed: 17     0 non-null     

In [4]:
muni_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 76 entries, 0 to 75
Data columns (total 11 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   OBJECTID      76 non-null     int32   
 1   MUNICUID      76 non-null     int32   
 2   MUNICID       76 non-null     object  
 3   NAME          76 non-null     object  
 4   FIPSCODE      48 non-null     float64 
 5   CREATEDBY     2 non-null      object  
 6   CREATEDDATE   2 non-null      object  
 7   MODIFIEDBY    11 non-null     object  
 8   MODIFIEDDATE  11 non-null     object  
 9   GlobalID      76 non-null     object  
 10  geometry      76 non-null     geometry
dtypes: float64(1), geometry(1), int32(2), object(7)
memory usage: 6.1+ KB


In [6]:
# %pip install geopandas shapely folium branca

import pandas as pd
import geopandas as gpd
import numpy as np
import folium
import branca

# ==============================================================
# 1) LOAD & CLEAN DATA
# ==============================================================

# assumes: deals_df (your 26k-row DataFrame) and muni_gdf (76-row GeoDataFrame)
deals = deals_df.copy()

# drop empty Unnamed columns
deals = deals[[c for c in deals.columns if not c.startswith("Unnamed:")]]

# normalize key fields
for col in ["latitude", "longitude", "price"]:
    deals[col] = pd.to_numeric(deals[col], errors="coerce")
deals = deals.dropna(subset=["latitude", "longitude", "price"])

deals["Agent_Name"] = deals["Agent_Name"].fillna("Unknown").replace("", "Unknown")
deals["Brokerage_Firm"] = deals["Brokerage_Firm"].fillna("Unknown").replace("", "Unknown")

# points GeoDataFrame
pts = gpd.GeoDataFrame(
    deals,
    geometry=gpd.points_from_xy(deals["longitude"], deals["latitude"]),
    crs="EPSG:4326"
)

# ==============================================================
# 2) PREPARE NEIGHBORHOOD POLYGONS
# ==============================================================

name_col = "NAME"  # change if your column differs
muni = muni_gdf.copy()
if muni.crs is None:
    muni = muni.set_crs("EPSG:4326", allow_override=True)
else:
    muni = muni.to_crs("EPSG:4326")

# dissolve by name to ensure uniqueness (avoid duplicate index problems)
muni_unique = muni.dissolve(by=name_col).reset_index()

# spatial join (points within polygons)
joined = gpd.sjoin(
    pts,
    muni_unique[[name_col, "geometry"]],
    how="inner",
    predicate="within"
).rename(columns={name_col: "neighborhood"})

# ==============================================================
# 3) BUILD AGGREGATION TABLES
# ==============================================================

def make_leader_table(df: pd.DataFrame, entity_col: str):
    grp = df.groupby(["neighborhood", entity_col], dropna=False).agg(
        deals=("Unique_ID", "count"),
        volume=("price", "sum")
    ).reset_index()

    totals = grp.groupby("neighborhood").agg(
        total_deals=("deals", "sum"),
        total_volume=("volume", "sum")
    ).reset_index()

    # leaders
    top_deals = grp.loc[grp.groupby("neighborhood")["deals"].idxmax(), ["neighborhood", entity_col, "deals"]]
    top_vol   = grp.loc[grp.groupby("neighborhood")["volume"].idxmax(), ["neighborhood", entity_col, "volume"]]

    out = totals.merge(
        top_deals.rename(columns={entity_col: "leader_deals_entity", "deals": "leader_deals"}),
        on="neighborhood", how="left"
    ).merge(
        top_vol.rename(columns={entity_col: "leader_volume_entity", "volume": "leader_volume"}),
        on="neighborhood", how="left"
    )

    out["share_deals"]  = np.where(out["total_deals"]  > 0, out["leader_deals"]  / out["total_deals"],  np.nan)
    out["share_volume"] = np.where(out["total_volume"] > 0, out["leader_volume"] / out["total_volume"], np.nan)
    return out

agent_tbl   = make_leader_table(joined, "Agent_Name")
broker_tbl  = make_leader_table(joined, "Brokerage_Firm")

def attach(muni_gdf, table):
    merged = muni_gdf.merge(table, left_on=name_col, right_on="neighborhood", how="left")
    return merged.set_index(name_col)

agent_poly  = attach(muni_unique, agent_tbl)
broker_poly = attach(muni_unique, broker_tbl)

# ==============================================================
# 4) SAFE VALUE GETTER (avoids ambiguous truth values)
# ==============================================================

def safe_get(df, idx, col):
    if idx not in df.index:
        return None
    val = df.loc[idx, col]
    if isinstance(val, (pd.Series, pd.DataFrame)):
        val = val.iloc[0] if not val.empty else None
    return val

# ==============================================================
# 5) CREATE MAP & LAYERS
# ==============================================================

center = [25.7617, -80.1918]
m = folium.Map(location=center, zoom_start=10, tiles="cartodbpositron", control_scale=True)

# add static legend
legend_html = """
<div style="
 position: fixed; bottom: 20px; left: 20px; z-index: 9999;
 background: white; padding: 10px 12px; border: 1px solid #bbb;
 font-size: 12px; box-shadow: 0 1px 4px rgba(0,0,0,0.2);">
 <b>Dominance Share</b><br>
 Leader’s share of deals or dollar volume within a neighborhood.<br>
 0% (weak) → 100% (strong)
</div>
"""
m.get_root().html.add_child(folium.Element(legend_html))

linear = branca.colormap.linear.YlGnBu_09.scale(0, 1)

def add_layer(gpoly, entity_label, metric_label, show_layer):
    metric_key = "deals" if metric_label == "Deals" else "volume"
    share_col  = f"share_{metric_key}"
    leader_ent_col = "leader_deals_entity" if metric_key == "deals" else "leader_volume_entity"
    leader_val_col = "leader_deals" if metric_key == "deals" else "leader_volume"
    total_col      = "total_deals"  if metric_key == "deals" else "total_volume"

    fg = folium.FeatureGroup(name=f"{entity_label} · {metric_label}", show=show_layer)

    def style_fn(feature):
        nm = feature["properties"].get(name_col)
        share_val = safe_get(gpoly, nm, share_col)
        if share_val is not None and pd.notnull(share_val):
            color = linear(float(share_val))
            return {"fillColor": color, "color": "#666", "weight": 0.8, "fillOpacity": 0.85}
        return {"fillColor": "#cccccc", "color": "#666", "weight": 0.8, "fillOpacity": 0.2}

    def popup_html(nm):
        share_val  = safe_get(gpoly, nm, share_col)
        if share_val is None or pd.isna(share_val):
            return f"<b>{nm}</b><br>No data."

        leader     = safe_get(gpoly, nm, leader_ent_col)
        leader_val = safe_get(gpoly, nm, leader_val_col)
        total_val  = safe_get(gpoly, nm, total_col)

        if metric_key == "deals":
            leader_txt = f"{int(leader_val):,} deals" if pd.notnull(leader_val) else "—"
            total_txt  = f"{int(total_val):,} deals"  if pd.notnull(total_val)  else "—"
        else:
            leader_txt = "${:,.0f}".format(leader_val) if pd.notnull(leader_val) else "—"
            total_txt  = "${:,.0f}".format(total_val)  if pd.notnull(total_val)  else "—"

        share_txt = f"{float(share_val)*100:.1f}%"
        return f"""
        <div style='font-size:13px'>
          <b>{nm}</b><br>
          <b>Leader {entity_label}:</b> {leader}<br>
          <b>Leader {metric_label}:</b> {leader_txt}<br>
          <b>Total {metric_label}:</b> {total_txt}<br>
          <b>Leader Share:</b> {share_txt}
        </div>
        """

    gj = folium.GeoJson(
        data=gpoly.reset_index().to_json(),
        style_function=style_fn,
        highlight_function=lambda f: {"weight": 2, "color": "#000"},
        tooltip=folium.GeoJsonTooltip(fields=[name_col], aliases=["Neighborhood:"], sticky=False)
    )

    for feat in gj.data["features"]:
        nm = feat["properties"].get(name_col)
        folium.Popup(popup_html(nm), max_width=260).add_to(gj)

    gj.add_to(fg)
    fg.add_to(m)

# add four toggleable layers
add_layer(agent_poly,   "Agent",     "Deals",          show_layer=True)
add_layer(agent_poly,   "Agent",     "Dollar Volume",  show_layer=False)
add_layer(broker_poly,  "Brokerage", "Deals",          show_layer=False)
add_layer(broker_poly,  "Brokerage", "Dollar Volume",  show_layer=False)

folium.LayerControl(position="topright", collapsed=False).add_to(m)

# ==============================================================
# 6) SAVE FOR WEB
# ==============================================================

m.save("index.html")
print("✅ Wrote index.html — open this file in a browser or embed via <iframe>")


✅ Wrote index.html — open this file in a browser or embed via <iframe>


In [7]:
m